<p><img src="imagenes/letragrama-rgb-150.jpg" width="380" align="left"><img src="imagenes/logoLCCazul.jpg" width="170" align="right"></p>

# [Curso de Redes Neuronales](https://curso-redes-neuronales-unison.github.io/Temario/)

# Red neuronal convolucional simple con tensorflow

[**Julio Waissman Vilanova**](http://mat.uson.mx/~juliowaissman/), 28 de noviembre de 2017.

En esta libreta intento explicar de forma simple como funciona el método sencillo de red neuronal convolucional usando *Tensorflow*. La explicación de la red convolucional ya está dada y en esta libreta solamente se explican los pasos necesarios para implementar una red convolucional simple explicando cada uno de sus pasos. Es básicamente una traducción, y puesta en forma de libreta del tutorial que viene en la página de *Tensorflow* y que se puede consultar [aquí](https://www.tensorflow.org/tutorials/layers).


Las redes convolucionales (CNN) son actualmente la arquitectura que mejores resultados he dado en problemas de reconocimiento de objetos en imágenes. La idea generar es aplicar una serie de filtros a la imagen original para extraer (por medio de aprendizaje) características de alto nivel, las cuales puedan ser útiles para el proceso de clasificacion de objetos en imágenes. Las CNN están conformadas típicamente por:

1. **Unidades convolucionales**. Las unidades convolucionales aplican filtros a la imágen y la convierten en un conjunto de imágenes tratadas a dimensión reducida, poniendo el acento en diferentes características. Estas unidades se componen a su vez de dos capas:

    1. **Capa convolucional**. La capa convolucional es uno o varios filtros los cuales se aplican a cada subregión al rededor de cada pixel con el fin de obtener una imagen tratada. Típicamente un filtro convolucional es un filtro lineal al cual al final se le aplica una no linearidad (típicamente una ReLU). Un factor importante del filtro es que los valores de la ventana del filtro se mantienen fijos a lo largo de toda la imagen (esto es, comparten *pesos* entre las diferentes subregiones).
    
    2. **Una capa de *pooling* **. La capa de pooling ayuda a reducir el muestreo de las imágenes generadas por los filtros, y reducir la dimensionalidad. Se basa en la idea que las salidas de los filtros se deben de parecer localmente y solo interesa un valor, el más significativo. El método de *pooling* más comúnes el máximo.
    
2. **Capas densas**. Estas se aplican después de una o varias capas convolucionales y son capas tipo *feedforward* donde todas las neuronas se conectn con todas. Es básicamente la etapa de clasificación, mientras que la anterior era la etápa de preprocesamiento de la imágen.

Por último, y en problemas de clasificación, la salida es una unidad *softmax* que permita discriminar entre diferentes tipos de salida posibles.






In [1]:
import numpy as np
import tensorflow as tf


La CNN que vamos a desarrollar (que es la arquitectura usada por LeNet) para clasificar el famosisimo y ya cansino conjunto de datos MNIST tiene la siguiente arquitectura:

1. Una unidad convolucional que contiene:
    1. 32 filtros de 5$\times$5 (en pixeles al rededor del pixel a filtrar), con activación ReLU.
    2. Una capa de *pooling* usando el máximo de una ventana de 2$\times$2 sin translape, por cada imágen generada.
2. Otra unidad convolucional que contiene:
    1. 64 filtros de 5$\times$5 con activación ReLU.
    2. Una capa de *pooling* usando el máximo de una ventana de 2$\times$2 sin translape, por cada imágen generada.
3. Una capa de neuronas tipo *feedforward* con 1,024 neuronas con activación ReLU.
4. Una capa de salida de 10 neuronas que compone una unidad *Softmax*.

Con el fin de mejorar la generalización, a la capa 3 (la capa oculta en *feedforward* se le aplica (en el aprendizaje) el método de *dropout* con una tasa de 0.4 (esto es, cualquier neurona puede ser retirada en forma aleatoria durante el aprendizaje con una probabilidad de 0.4).

Vamos a armar este modelo con el uso de las facilidades que da `tf.layers`, que nos permiten hacer una capa de una CNN en una sola linea. Rápido, bonito y efectivo. Vamos a ver como se diseña la arquitectura de la CNN descrita:

In [2]:
def modelo_cnn_mnist(features, labels, mode):
    """
    Modelo de la CNN descrita arriba
    """
    
    # Capa de entrada: 
    # Convierte un vector de datos en un tensor [batch, ancho, alto, canales]
    # Donde canales son las capas de la imagen (por ejemplo RGB)
    # En este caso las imagenes son en BW (un solo canal)
    # y de 24 x 24 pixeles.
    # 
    # batch = -1 significa que lo calcula al vuelo para completar.
    capa_entrada = tf.reshape(features["x"], [-1, 28, 28, 1])

    # 1ra capa convolucional
    # 32 filtros de 5x5 y salida ReLU
    # padding puede ser "same", lo que implica que calcula el filtro
    # inclusive para las orillas, si padding=valid entonces no calcula 
    # el filtro en las orillas, completando con 0s.
    # 
    # En este caso si la entrada a la capa es de dimensión [-1, 28, 28, 1]
    # la salida de la capa es [-1, 28, 28, 32]
    conv1 = tf.layers.conv2d(
        inputs=capa_entrada,
        filters=32,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)

    # 1ra capa max pool, sin translape (strides = poolsize[0] = poolsize[1])
    # Si la entrada a la capa era de dimensiones [-1, 28, 28, 32]
    # la salida es [-1, 14, 14, 32]
    pool1 = tf.layers.max_pooling2d(
        inputs=conv1, 
        pool_size=[2, 2], 
        strides=2)

    # 2da capa convolucional
    # 64 filtros de 5x5 y salida ReLU
    # Si la entrada a la capa es de la forma [-1, 14, 14, 32]
    # La salida es de la forma [-1, 14, 14, 64]
    conv2 = tf.layers.conv2d(
        inputs=pool1,
        filters=64,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)

    # 2da capa max pool, sin translape (strides = poolsize[0] = poolsize[1])
    # Si la entrada a la capa era de dimensiones [-1, 14, 14, 64]
    # la salida es [-1, 7, 7, 64]
    pool2 = tf.layers.max_pooling2d(
        inputs=conv2, 
        pool_size=[2, 2], 
        strides=2)


    # Capa densamente conectada con 1024 unidades linealmente rectificadas
    pool2_estirado = tf.reshape(pool2, [-1, 7 * 7 * 64])
    capa_densa = tf.layers.dense(
        inputs=pool2_estirado, 
        units=1024, 
        activation=tf.nn.relu)

    # Agregamos el dropout aqui (esto ya empieza a ser bizarro)
    # En los modelos se pone la arquitectura, la forma de aprendizaje y estimación,
    # así que si requerimos dropout en una capa hay que ponerlo aqui en forma explicita.
    #
    # Notese que decimos que solo si estamos en modo entrenamiento es que aplicamos el dropout
    dropout = tf.layers.dropout(
        inputs=capa_densa, 
        rate=0.4, 
        training=mode == tf.estimator.ModeKeys.TRAIN)

    # Capa de salida
    # Dimensión de la entrada: [-1, 1024]
    # y la salida es de [-1, 10]
    logits = tf.layers.dense(inputs=dropout, units=10)

    
    # Listo! Ya esta la arquitectura general, ahora hay que definir claramente las cosas 
    # para los diferentes modos de operación (así funcionan los modelos que se usan preentrenados)
    # Los modos de operación son 3: PREDICT, TRAIN, EVAL.

    predicciones = {
        # Realiza la predicción (para los modos preestablecidos PREDICT y EVAL)
        # En este caso nos interesa la clase retenida y la probabilidad de cada una
        "clases": tf.argmax(input=logits, axis=1),
        "probabilidades": tf.nn.softmax(logits, name="softmax_tensor")
    }

    # Y para la predicción tenemos lo necesario
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, 
                                          predictions=predicciones)

    # Calcula la función de pérdida (para los modos TRAIN y EVAL)
    onehot_labels = tf.one_hot(indices=tf.cast(labels, tf.int32), depth=10)

    loss = tf.losses.softmax_cross_entropy(
        onehot_labels=onehot_labels, 
        logits=logits)

    # Completa lo necesario para el modo TRAIN (método de optimización)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizador = tf.train.GradientDescentOptimizer(learning_rate=0.001)

        entrenamiento = optimizador.minimize(loss=loss, 
                                             global_step=tf.train.get_global_step())

        return tf.estimator.EstimatorSpec(mode=mode, 
                                          loss=loss, 
                                          train_op=entrenamiento)

    # Acaba con las operaciones del modo EVAL
    evaluacion = {
        "accuracy": tf.metrics.accuracy(labels=labels, 
                                        predictions=predicciones["clases"])}
    return tf.estimator.EstimatorSpec(mode=mode, 
                                      loss=loss, 
                                      eval_metric_ops=evaluacion)


Como podemos ver, acabamos de definir un modelo completo como función, el cual debe de llevar **con esos mismos nombres**, las entradas *features*, *labels*, *mode* (si las traducen al español, se enclocha).

El modelo debe de incluir lo siguiente:

1. La arquitectura bien definida desde las entradas a las salidas, los tipos de capas, número de neuronas y form de procesar.

2. El método de evaluación utilizando salida *softmax* y asumiendo que la clase mas probable es la clase seleccionada.

3. El método de aprendizaje (descenso de gradiente con tasa de aprendizaje de 0.001). 

4. El método de medición de error (o perdida) utilizando la entropía.

5. La función de evaluación, basada en la exactitud (una de las pruebas más básicas posibles).

Las operaciones necesarias para el modo PREDICT son 1 y 2, mientras que las operaciones necesarias para el modo TRAIN son 1, 3 y 4, y para el modo TEST se requieren 1, 2 y 5. Con el fin de ahorrar en tiempo de computo, solamente se asignan las operaciones que importan para cada modo.

Vamos a aplicar para aprendizaje y reconocimiento, en el conjunto de base de pruebas que empieza a aburrirnos.

In [3]:
mnist = tf.contrib.learn.datasets.load_dataset("mnist")

datos_entrenamiento = mnist.train.images  
salidas_entrenamiento = np.asarray(mnist.train.labels, dtype=np.int32)

datos_prueba = mnist.test.images  # Returns np.array
salidas_prueba = np.asarray(mnist.test.labels, dtype=np.int32)


Extracting MNIST-data\train-images-idx3-ubyte.gz
Extracting MNIST-data\train-labels-idx1-ubyte.gz
Extracting MNIST-data\t10k-images-idx3-ubyte.gz
Extracting MNIST-data\t10k-labels-idx1-ubyte.gz


Así es, tenemos la horrorosa base de datos de MNIST, a la cual le vamos a aplicar nuestro modelo

In [4]:
# El modelo que vamos a utilizar y la dirección para guardar el log
clasificador = tf.estimator.Estimator(
    model_fn=modelo_cnn_mnist, 
    model_dir="./cnn_log")


INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': './cnn_log', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x000000001033F7B8>, '_task_type': 'worker', '_task_id': 0, '_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


Ahora vamos a entrenar, y para eso vamos a guardar en un registro (log) el proceso de aprendizaje, por lo que vamos a hacer un log descriptivo (*verbose*), así como definir cuales son las entradas con las que se va a aprender.

In [5]:
# Para guardar y desplegar la información a lo largo del aprendizaje
tf.logging.set_verbosity(tf.logging.INFO)
tensors_to_log = {"probabilidades": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, 
                                          every_n_iter=50)


# La función que define que se le pone al entrenamiento

entrada_entrenamiento = tf.estimator.inputs.numpy_input_fn(
    x={"x": datos_entrenamiento},
    y=salidas_entrenamiento,
    batch_size=100,
    num_epochs=None,
    shuffle=True)

clasificador.train(
    input_fn=entrada_entrenamiento,
    steps=20000,
    hooks=[logging_hook])



Instructions for updating:

Future major versions of TensorFlow will allow gradients to flow
into the labels input on backprop by default.

See tf.nn.softmax_cross_entropy_with_logits_v2.

INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into ./cnn_log\model.ckpt.
INFO:tensorflow:probabilidades = [[0.08640128 0.11296035 0.08193345 0.10267363 0.09160786 0.10615633
  0.0931919  0.11087248 0.1126813  0.10152147]
 [0.11026498 0.12132239 0.0657806  0.09507556 0.10114555 0.11502858
  0.09073588 0.09971913 0.11653855 0.0843887 ]
 [0.11260471 0.12410452 0.07899853 0.08546712 0.09019461 0.11062732
  0.09163798 0.10001292 0.11241261 0.0939396 ]
 [0.11026352 0.11049809 0.07340105 0.09021442 0.10070555 0.11054579
  0.08558346 0.10549863 0.10510734 0.10818219]
 [0.08560502 0.11388909 0.08466665 0.10450007 0.08659182 0.1175632
  0.09795086 0.1056543  0.11135725 0.09222184]
 [0.08929683 0.10538702 0.08261897 0.09880549 0.08789487 0.11099561
  0.09312505 0.11426585 

INFO:tensorflow:loss = 2.296274, step = 1
INFO:tensorflow:probabilidades = [[0.0946656  0.1031407  0.08386552 0.09968922 0.09696145 0.09684217
  0.10542125 0.10845169 0.11731087 0.09365143]
 [0.08745989 0.10206693 0.08264977 0.1095444  0.09687021 0.11763801
  0.08834893 0.10391441 0.12146611 0.09004131]
 [0.09502247 0.10995248 0.08031467 0.10327046 0.09538376 0.09908608
  0.09600735 0.09742875 0.12287499 0.10065897]
 [0.10763412 0.11131532 0.07982006 0.09647921 0.10454914 0.11171918
  0.07711817 0.10027698 0.11566604 0.09542179]
 [0.09195399 0.10561656 0.08926138 0.08936545 0.10134362 0.10672027
  0.10248807 0.09893395 0.11136796 0.10294881]
 [0.09576108 0.11079765 0.0829498  0.09202313 0.09747713 0.10661032
  0.10047957 0.09688222 0.11714701 0.09987202]
 [0.09684597 0.10796443 0.09172583 0.10517745 0.09046663 0.10850313
  0.09551434 0.10280317 0.10882364 0.09217545]
 [0.09832399 0.09745185 0.08257397 0.11617817 0.09755027 0.11032409
  0.08531356 0.1010853  0.12419253 0.08700626]
 [0.0

INFO:tensorflow:global_step/sec: 2.08778
INFO:tensorflow:probabilidades = [[0.1036172  0.10662385 0.08808507 0.09438235 0.09251452 0.10073873
  0.10640538 0.09720986 0.10715232 0.10327065]
 [0.097303   0.11133987 0.08238278 0.09473369 0.09134594 0.10371953
  0.09397742 0.10613798 0.11773343 0.10132635]
 [0.09179823 0.09483021 0.08658223 0.09890909 0.10255789 0.11824207
  0.10412451 0.09894858 0.10268566 0.1013215 ]
 [0.09961082 0.1077904  0.08632769 0.09980467 0.09900105 0.12267054
  0.09225572 0.09249809 0.10105884 0.09898221]
 [0.09700994 0.11237736 0.08287714 0.100906   0.09317617 0.10745403
  0.09891034 0.09131742 0.12476235 0.0912093 ]
 [0.10344515 0.10536143 0.09080493 0.09325668 0.08651426 0.10759537
  0.09261727 0.1011116  0.11647407 0.10281921]
 [0.09537755 0.10725678 0.09044477 0.10000058 0.09613087 0.10085413
  0.09871427 0.10009184 0.11216708 0.0989622 ]
 [0.08575964 0.11137871 0.07193883 0.10356329 0.10086258 0.11551825
  0.09659048 0.10635432 0.11233447 0.09569942]
 [0.08

INFO:tensorflow:loss = 2.297186, step = 101 (47.896 sec)
INFO:tensorflow:probabilidades = [[0.1100578  0.10924629 0.08285686 0.09686548 0.09721978 0.11060271
  0.09603816 0.0910525  0.11602768 0.09003267]
 [0.11396939 0.10866567 0.07747804 0.10594367 0.10546351 0.10609945
  0.08361133 0.09943163 0.10449556 0.09484189]
 [0.0976653  0.1088319  0.08346428 0.09901041 0.09624462 0.09916592
  0.09859131 0.09678735 0.1119329  0.10830605]
 [0.08818961 0.10594161 0.07708696 0.09989735 0.102332   0.10458271
  0.08838854 0.11343963 0.11643986 0.1037018 ]
 [0.09878729 0.1037954  0.08425672 0.10017175 0.0908236  0.1275629
  0.09873325 0.09010417 0.11066195 0.095103  ]
 [0.09592733 0.11315266 0.09162199 0.10361954 0.09301265 0.10354429
  0.086154   0.11187417 0.10305595 0.09803747]
 [0.09261917 0.08378541 0.08145326 0.09816786 0.10342494 0.11202896
  0.08711538 0.10386146 0.11978363 0.1177599 ]
 [0.11091843 0.09400143 0.08026269 0.1114305  0.09368291 0.10093006
  0.09518237 0.09916241 0.10008798 0.1

INFO:tensorflow:global_step/sec: 2.09922
INFO:tensorflow:probabilidades = [[0.10160723 0.11546752 0.08723515 0.10693628 0.09526449 0.08899938
  0.10592633 0.09244721 0.11568131 0.09043507]
 [0.1034952  0.09255658 0.08519083 0.09226446 0.09920514 0.11396938
  0.09182588 0.11412816 0.10923593 0.09812846]
 [0.1042387  0.08948864 0.10366242 0.10909176 0.08476905 0.10645276
  0.09330855 0.10592628 0.10826767 0.09479409]
 [0.08064418 0.11138926 0.08108938 0.10453761 0.09785311 0.09934308
  0.10910709 0.10635947 0.11254846 0.0971283 ]
 [0.09579532 0.10245042 0.08113045 0.11075155 0.09417437 0.09943192
  0.10053047 0.09939554 0.1120814  0.10425856]
 [0.09270296 0.10112093 0.0786382  0.09964172 0.09703128 0.09831733
  0.11428382 0.1089414  0.10863624 0.10068617]
 [0.09734395 0.10772877 0.07925805 0.09916368 0.10504431 0.10798995
  0.09752911 0.09075325 0.1145274  0.10066153]
 [0.09869411 0.09518812 0.10671897 0.10490578 0.08908011 0.09770238
  0.11290824 0.08803521 0.10922144 0.09754566]
 [0.09

...

INFO:tensorflow:global_step/sec: 2.36367
INFO:tensorflow:probabilidades = [[0.0277555  0.00185    0.02369277 0.01683909 0.74777335 0.01730634
  0.01073818 0.0049153  0.00723204 0.14189741]
 [0.04447493 0.00314813 0.09715977 0.00190837 0.32847467 0.01199943
  0.28039208 0.05602771 0.03882124 0.13759358]
 [0.00000015 0.00001921 0.00004547 0.0010703  0.00000176 0.00000232
  0.         0.9986638  0.00000463 0.00019239]
 [0.00022501 0.00004218 0.97634596 0.01882678 0.00003985 0.00001404
  0.00001958 0.00182456 0.00224664 0.00041538]
 [0.0000545  0.99767107 0.00014124 0.00007381 0.00028735 0.00002411
  0.00001475 0.00123776 0.00045718 0.00003815]
 [0.00000028 0.         0.00000018 0.00000355 0.9932846  0.00001166
  0.00000028 0.00001431 0.00009245 0.00659282]
 [0.00000212 0.00000128 0.00001484 0.0005134  0.01086202 0.00005746
  0.00000027 0.0004519  0.00025782 0.98783886]
 [0.00000011 0.00001499 0.00003867 0.00000376 0.9997131  0.00008606
  0.00002474 0.0000085  0.00004837 0.00006166]
 [0.00

INFO:tensorflow:loss = 0.092907004, step = 19801 (42.354 sec)
INFO:tensorflow:probabilidades = [[0.000006   0.00000096 0.00000236 0.00004038 0.00120944 0.00160551
  0.00000026 0.99447566 0.00010905 0.00255035]
 [0.00000533 0.00424618 0.01630403 0.00813783 0.01932488 0.00178218
  0.00129749 0.9013332  0.04549858 0.00207027]
 [0.00000001 0.         0.00000027 0.00000042 0.00000002 0.00000001
  0.         0.99985504 0.00000078 0.0001434 ]
 [0.00730006 0.00150326 0.00047066 0.06515388 0.00005998 0.9087854
  0.00006188 0.00098666 0.00284692 0.01283137]
 [0.00000144 0.00001947 0.00002977 0.00044552 0.00000093 0.00000117
  0.         0.99938965 0.00000509 0.00010703]
 [0.00003223 0.00066488 0.95800334 0.00011469 0.0368942  0.00003662
  0.00420287 0.00001416 0.00002923 0.0000078 ]
 [0.0000124  0.00000016 0.00001317 0.00000032 0.00001327 0.00002112
  0.999938   0.         0.00000157 0.        ]
 [0.00001388 0.00127603 0.07335433 0.92352384 0.00000525 0.00023734
  0.00000915 0.00002936 0.0015450

INFO:tensorflow:global_step/sec: 2.37231
INFO:tensorflow:probabilidades = [[0.00000073 0.         0.0000008  0.         0.0000018  0.00000028
  0.9999963  0.00000001 0.00000008 0.        ]
 [0.0000001  0.00000001 0.00000154 0.00000567 0.00000001 0.00000005
  0.         0.99986196 0.00000009 0.00013051]
 [0.00000044 0.00012727 0.00021814 0.00005724 0.99757737 0.00006248
  0.00005573 0.00004984 0.00055285 0.00129863]
 [0.00009215 0.00002994 0.99711263 0.00258067 0.00012827 0.00000332
  0.00003188 0.00000209 0.00001631 0.00000269]
 [0.00000354 0.00000002 0.00000033 0.00082239 0.00017585 0.99709415
  0.00002088 0.00000035 0.00000974 0.00187267]
 [0.00000089 0.00000077 0.00000267 0.00002279 0.0324169  0.00004334
  0.00000001 0.00136439 0.0003252  0.96582305]
 [0.00065791 0.00463909 0.00108829 0.8381913  0.00040241 0.0470987
  0.00000874 0.01379037 0.00034701 0.09377629]
 [0.99997747 0.         0.00001447 0.00000004 0.         0.00000369
  0.00000058 0.00000022 0.00000003 0.00000363]
 [0.000

INFO:tensorflow:loss = 0.1119693, step = 19901 (42.122 sec)
INFO:tensorflow:probabilidades = [[0.00067034 0.01014166 0.00437807 0.23120601 0.00839493 0.0632413
  0.00159332 0.00072187 0.6283493  0.05130321]
 [0.00000888 0.00000534 0.00063813 0.00000016 0.00003185 0.00000656
  0.9993082  0.         0.00000074 0.00000007]
 [0.0095955  0.00000092 0.0005011  0.00000155 0.97367543 0.00036114
  0.00270217 0.0002242  0.00922014 0.00371793]
 [0.00029007 0.12601677 0.0008949  0.0181352  0.00257684 0.00059499
  0.0000751  0.01712283 0.71056855 0.12372472]
 [0.00156082 0.91761625 0.00169112 0.00452696 0.00205851 0.00034572
  0.00253589 0.00016081 0.06947254 0.00003148]
 [0.0049514  0.00016327 0.00690571 0.00000315 0.00000007 0.00003985
  0.98793507 0.         0.00000156 0.        ]
 [0.00002317 0.99443394 0.0000526  0.0001854  0.00012786 0.00013596
  0.00005663 0.00011552 0.00483737 0.00003159]
 [0.0003253  0.05029095 0.1353804  0.8122337  0.00000454 0.00015464
  0.00000797 0.00120561 0.00037734 

INFO:tensorflow:Saving checkpoints for 20000 into ./cnn_log\model.ckpt.
INFO:tensorflow:Loss for final step: 0.109583646.


Y ahora aplicamos los modos de predicción y prueba

In [7]:
entrada_prueba = tf.estimator.inputs.numpy_input_fn(
    x={"x": datos_prueba},
    y=salidas_prueba,
    num_epochs=1,
    shuffle=False)

eval_results = clasificador.evaluate(input_fn=entrada_prueba)
  
print(eval_results)

INFO:tensorflow:Starting evaluation at 2018-05-30-07:21:08
INFO:tensorflow:Restoring parameters from ./cnn_log\model.ckpt-20000
INFO:tensorflow:Finished evaluation at 2018-05-30-07:21:23
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9684, global_step = 20000, loss = 0.10185103
{'accuracy': 0.9684, 'loss': 0.10185103, 'global_step': 20000}
